In [6]:
%matplotlib notebook

In [7]:
import numpy as np
import matplotlib.pyplot as plt
from scipy.integrate import solve_ivp

# Define the damped pendulum equation
def damped_pendulum(t, y, b, c):
    theta, omega = y
    dydt = [omega, -b * omega - c * np.sin(theta)]
    return dydt

# Parameters
b = 0.0  # Damping coefficient
c = 9.81  # Gravity constant (assuming unit length)
y0 = [np.pi / 2, 0]  # Initial condition: [initial angle, initial angular velocity]
t_span = (0, 10)  # Time range
t_eval = np.linspace(*t_span, 300)  # Time points for evaluation

# Solve the differential equation
sol = solve_ivp(damped_pendulum, t_span, y0, t_eval=t_eval, args=(b, c))

# Plot the results
plt.figure(figsize=(10, 5))
plt.plot(sol.t, sol.y[0], label='Angle (theta)')
plt.plot(sol.t, sol.y[1], label='Angular velocity (omega)')
plt.xlabel('Time (s)')
plt.ylabel('Values')
plt.title('Damped Pendulum Dynamics')
plt.legend()
plt.grid()
plt.show()

<IPython.core.display.Javascript object>

In [8]:
# Phase portrait of the damped pendulum

plt.figure(figsize=(6, 6))
plt.plot(sol.y[0], sol.y[1], color='b')
plt.xlabel('Angle (theta)')
plt.ylabel('Angular velocity (omega)')
plt.title('Phase Portrait of the Damped Pendulum')
plt.grid()
plt.show()

# Animation of the damped pendulum

import matplotlib.animation as animation

fig, ax = plt.subplots(figsize=(5, 5))
ax.set_xlim(-1.2, 1.2)
ax.set_ylim(-1.2, 1.2)
ax.set_xlabel('X')
ax.set_ylabel('Y')
ax.set_title('Damped Pendulum Animation')

line, = ax.plot([], [], 'o-', lw=2)

def init():
    line.set_data([], [])
    return line,

def update(i):
    x = np.sin(sol.y[0][i])
    y = -np.cos(sol.y[0][i])
    line.set_data([0, x], [0, y])
    return line,

ani = animation.FuncAnimation(fig, update, frames=len(sol.t), init_func=init, blit=True, interval=30)

plt.show()

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [10]:
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as animation
from scipy.integrate import solve_ivp
from IPython.display import HTML

# Define the damped pendulum equation
def damped_pendulum(t, y, b, c):
    theta, omega = y
    dydt = [omega, -b * omega - c * np.sin(theta)]
    return dydt

# Parameters
b = 0.0  # Damping coefficient
c = 9.81  # Gravity (assuming length = 1)
y0 = [np.pi / 2, 0]  # Initial condition: [initial angle, initial angular velocity]
t_span = (0, 10)  # Time range
t_eval = np.linspace(*t_span, 300)  # Time points for evaluation

# Solve the differential equation
sol = solve_ivp(damped_pendulum, t_span, y0, t_eval=t_eval, args=(b, c))

# Extract angle values
theta_vals = sol.y[0]

# Convert theta to Cartesian coordinates
x_vals = np.sin(theta_vals)
y_vals = -np.cos(theta_vals)

# Set up the figure and axis
fig, ax = plt.subplots(figsize=(5, 5))
ax.set_xlim(-1.2, 1.2)
ax.set_ylim(-1.2, 1.2)
ax.set_xlabel('X')
ax.set_ylabel('Y')
ax.set_title('Damped Pendulum Animation')

# Initialize the pendulum line
line, = ax.plot([], [], 'o-', lw=2)

# Function to initialize the animation
def init():
    line.set_data([], [])
    return line,

# Function to update the animation frame
def update(i):
    line.set_data([0, x_vals[i]], [0, y_vals[i]])
    return line,

# Create the animation
ani = animation.FuncAnimation(fig, update, frames=len(sol.t), init_func=init, blit=True, interval=30)

# Display animation in Jupyter Notebook
HTML(ani.to_jshtml())

<IPython.core.display.Javascript object>

In [ ]:
import torch
import torch.nn as nn
import torch.optim as optim
from torch.autograd import grad
import numpy as np
import matplotlib.pyplot as plt
from scipy.integrate import solve_ivp

# Generate training data for the damped pendulum
def damped_pendulum(t, y, b, c):
    q, p = y
    dqdt = p
    dpdt = -c * np.sin(q) - b * p
    return [dqdt, dpdt]

# Parameters
b = 0.2  # Damping coefficient
c = 9.81  # Gravity
y0 = [np.pi / 2, 0]  # Initial condition
t_span = (0, 10)
t_eval = np.linspace(*t_span, 300)

# Solve the system
sol = solve_ivp(damped_pendulum, t_span, y0, t_eval=t_eval, args=(b, c))
q_train, p_train = sol.y

# Convert data to PyTorch tensors
q_train = torch.tensor(q_train, dtype=torch.float32).reshape(-1, 1)
p_train = torch.tensor(p_train, dtype=torch.float32).reshape(-1, 1)
data_train = torch.cat((q_train, p_train), dim=1)

# Define the Hamiltonian Neural Network
class HamiltonianNN(nn.Module):
    def __init__(self):
        super(HamiltonianNN, self).__init__()
        self.net = nn.Sequential(
            nn.Linear(2, 32),
            nn.Tanh(),
            nn.Linear(32, 32),
            nn.Tanh(),
            nn.Linear(32, 1)  # Outputs the Hamiltonian
        )

    def forward(self, q, p):
        H = self.net(torch.cat((q, p), dim=1))
        return H

# Initialize model, optimizer, and loss function
model = HamiltonianNN()
optimizer = optim.Adam(model.parameters(), lr=0.01)

# Training loop
epochs = 5000
for epoch in range(epochs):
    optimizer.zero_grad()

    q, p = data_train[:, 0:1], data_train[:, 1:2]
    q.requires_grad_(True)
    p.requires_grad_(True)

    H = model(q, p)
    dH_dq = grad(H.sum(), q, create_graph=True)[0]
    dH_dp = grad(H.sum(), p, create_graph=True)[0]

    # Hamiltonian equations with damping term
    dq_pred = dH_dp
    dp_pred = -dH_dq - b * p

    # Compute loss
    loss = torch.mean((dq_pred - p) ** 2 + (dp_pred + c * torch.sin(q) + b * p) ** 2)
    loss.backward()
    optimizer.step()

    if epoch % 500 == 0:
        print(f"Epoch {epoch}, Loss: {loss.item()}")

# Test the learned Hamiltonian
q_test = torch.linspace(-np.pi, np.pi, 100).reshape(-1, 1)
p_test = torch.linspace(-2, 2, 100).reshape(-1, 1)
q_mesh, p_mesh = torch.meshgrid(q_test.flatten(), p_test.flatten())

q_input = q_mesh.reshape(-1, 1)
p_input = p_mesh.reshape(-1, 1)
H_pred = model(q_input, p_input).detach().numpy().reshape(100, 100)

# Plot the learned Hamiltonian
plt.figure(figsize=(8, 6))
plt.contourf(q_mesh.numpy(), p_mesh.numpy(), H_pred, levels=30, cmap="viridis")
plt.colorbar(label="Hamiltonian")
plt.xlabel("Angle (q)")
plt.ylabel("Momentum (p)")
plt.title("Learned Hamiltonian for the Damped Pendulum")
plt.show()

In [ ]:
import torch
import torch.nn as nn
import torch.optim as optim
import numpy as np
import matplotlib.pyplot as plt
from scipy.integrate import solve_ivp

# Define the governing equation for the damped pendulum
b = 0.2  # Damping coefficient
c = 9.81  # Gravity constant
t_span = (0, 10)
t_train = torch.linspace(*t_span, 300).reshape(-1, 1)  # Training time points

# Solve the system using a numerical ODE solver for comparison
def damped_pendulum(t, y, b, c):
    theta, omega = y
    return [omega, -b * omega - c * np.sin(theta)]

y0 = [np.pi / 2, 0]  # Initial conditions
sol = solve_ivp(damped_pendulum, t_span, y0, t_eval=t_train.numpy().flatten(), args=(b, c))
theta_true = torch.tensor(sol.y[0], dtype=torch.float32).reshape(-1, 1)

lambda1, lambda2 = 1e-1, 1e-4  # Regularization parameters

# Define the PINN model
class PINN(nn.Module):
    def __init__(self):
        super(PINN, self).__init__()
        self.net = nn.Sequential(
            nn.Linear(1, 32),
            nn.Tanh(),
            nn.Linear(32, 32),
            nn.Tanh(),
            nn.Linear(32, 1)
        )

    def forward(self, t):
        return self.net(t)

# Initialize the model and optimizer
model = PINN()
optimizer = optim.Adam(model.parameters(), lr=0.01)

# Training loop
epochs = 15000
for epoch in range(epochs):
    optimizer.zero_grad()

    t = t_train.clone().requires_grad_(True)
    theta_pred = model(t)

    # Initial condition loss
    u_boundary = theta_pred[0]  # Evaluate network at t = 0
    loss1 = (torch.squeeze(u_boundary) - np.pi / 2) ** 2  # Enforce theta(0) = pi/2

    # Compute derivative u'(0) via autograd
    dudt_boundary = torch.autograd.grad(
        outputs=u_boundary,
        inputs=t,
        grad_outputs=torch.ones_like(u_boundary),
        create_graph=True
    )[0][0]  # Ensure we get a scalar

    loss2 = (torch.squeeze(dudt_boundary) - 0) ** 2  # Enforce theta'(0) = 0

    # Compute derivatives using autograd
    theta_t = torch.autograd.grad(theta_pred, t, torch.ones_like(theta_pred), create_graph=True)[0]
    theta_tt = torch.autograd.grad(theta_t, t, torch.ones_like(theta_t), create_graph=True)[0]

    # Compute the physics-informed loss (forcing the neural network to satisfy the ODE)
    residual = theta_tt + b * theta_t + c * torch.sin(theta_pred)
    loss_pde = torch.mean(residual ** 2)

    # Total loss
    loss = loss_pde + lambda1 * loss1 + lambda2 * loss2

    # Backpropagation
    loss.backward()
    optimizer.step()

    if epoch % 500 == 0:
        print(f"Epoch {epoch}, Loss: {loss.item()}")

# Generate predictions
theta_pinn = model(t_train).detach().numpy()

# Plot results
plt.figure(figsize=(10, 5))
plt.plot(t_train.numpy(), theta_true.numpy(), label="True Solution (ODE Solver)", linewidth=2)
plt.plot(t_train.numpy(), theta_pinn, label="PINN Approximation", linestyle="dashed")
plt.xlabel("Time (s)")
plt.ylabel("Theta (rad)")
plt.title("Damped Pendulum: PINN vs ODE Solver")
plt.legend()
plt.grid()
plt.show()

In [ ]:
import torch
import torch.nn as nn
import torch.optim as optim
import numpy as np
import matplotlib.pyplot as plt
from scipy.integrate import solve_ivp

# Define the governing equation for the damped pendulum
true_b = 0.2  # True damping coefficient (unknown to the model)
c = 9.81  # Gravity constant
t_span = (0, 10)
t_train = torch.linspace(*t_span, 300).reshape(-1, 1)  # Training time points

# Solve the system using a numerical ODE solver for comparison
def damped_pendulum(t, y, b, c):
    theta, omega = y
    return [omega, -b * omega - c * np.sin(theta)]

y0 = [np.pi / 2, 0]  # Initial conditions
sol = solve_ivp(damped_pendulum, t_span, y0, t_eval=t_train.numpy().flatten(), args=(true_b, c))

# Add noise to simulate measurement errors
noise_std = 0.05  # Noise standard deviation
theta_noisy = sol.y[0] + noise_std * np.random.randn(*sol.y[0].shape)
theta_noisy = torch.tensor(theta_noisy, dtype=torch.float32).reshape(-1, 1)

# Define the PINN model with learnable damping coefficient
class PINN(nn.Module):
    def __init__(self):
        super(PINN, self).__init__()
        self.net = nn.Sequential(
            nn.Linear(1, 32),
            nn.Tanh(),
            nn.Linear(32, 32),
            nn.Tanh(),
            nn.Linear(32, 1)
        )
        self.b = nn.Parameter(torch.tensor(0.5, dtype=torch.float32))  # Initialize with arbitrary guess

    def forward(self, t):
        return self.net(t)

# Initialize the model and optimizer
model = PINN()
optimizer = optim.Adam(model.parameters(), lr=0.001)

lambda1, lambda2, lambda3 = 1e-1, 1e-4, 1e-0  # Regularization parameters

# Training loop
epochs = 100000
for epoch in range(epochs):
    optimizer.zero_grad()

    t = t_train.clone().requires_grad_(True)
    theta_pred = model(t)

    # Compute derivatives
    theta_t = torch.autograd.grad(theta_pred, t, torch.ones_like(theta_pred), create_graph=True)[0]
    theta_tt = torch.autograd.grad(theta_t, t, torch.ones_like(theta_t), create_graph=True)[0]

    # Compute the physics-informed loss (forcing the neural network to satisfy the ODE)
    residual = theta_tt + model.b * theta_t + c * torch.sin(theta_pred)
    loss_pde = torch.mean(residual ** 2)

    # Initial condition loss
    u_boundary = theta_pred[0]  # Evaluate network at t = 0
    loss1 = (torch.squeeze(u_boundary) - np.pi / 2) ** 2  # Enforce theta(0) = pi/2

    # Compute derivative u'(0) via autograd
    dudt_boundary = torch.autograd.grad(
        outputs=u_boundary,
        inputs=t,
        grad_outputs=torch.ones_like(u_boundary),
        create_graph=True
    )[0][0]  # Ensure we get a scalar

    loss2 = (torch.squeeze(dudt_boundary) - 0) ** 2  # Enforce theta'(0) = 0

    # Data loss (matching the noisy data)
    loss_data = torch.mean((theta_pred - theta_noisy) ** 2)

    # Total loss
    loss = loss_pde + lambda1 * loss1 + lambda2 * loss2 + lambda3 * loss_data

    # Backpropagation
    loss.backward()
    optimizer.step()

    if epoch % 2500 == 0:
        print(f"Epoch {epoch}, Loss: {loss.item()}, Learned b: {model.b.item()}")

# Generate predictions
theta_pinn = model(t_train).detach().numpy()

# Plot results
plt.figure(figsize=(10, 5))
plt.plot(t_train.numpy(), sol.y[0], label="True Solution (ODE Solver)", linewidth=2, color='blue')
plt.scatter(t_train.numpy(), theta_noisy.numpy(), label="Noisy Data", color='red', s=10, alpha=0.6)
plt.plot(t_train.numpy(), theta_pinn, label="PINN Approximation", linestyle="dashed", color='green')
plt.xlabel("Time (s)")
plt.ylabel("Theta (rad)")
plt.title(f"Damped Pendulum: PINN vs Noisy Data (Learned b = {model.b.item():.4f})")
plt.legend()
plt.grid()
plt.show()

In [ ]:
t_span = (0, 50)
t_train = torch.linspace(*t_span, 5000).reshape(-1, 1)  # Training time points

# Generate predictions
theta_pinn = model(t_train).detach().numpy()

y0 = [np.pi / 2, 0]  # Initial conditions
sol = solve_ivp(damped_pendulum, t_span, y0, t_eval=t_train.numpy().flatten(), args=(true_b, c))

# Plot results
plt.figure(figsize=(10, 5))
plt.plot(t_train.numpy(), sol.y[0], label="True Solution (ODE Solver)", linewidth=2, color='blue')
# plt.scatter(t_train.numpy(), theta_noisy.numpy(), label="Noisy Data", color='red', s=10, alpha=0.6)
plt.plot(t_train.numpy(), theta_pinn, label="PINN Approximation", linestyle="dashed", color='green')
plt.xlabel("Time (s)")
plt.ylabel("Theta (rad)")
plt.title(f"Damped Pendulum: PINN vs Noisy Data (Learned b = {model.b.item():.4f})")
plt.legend()
plt.grid()
plt.show()

In [ ]:
import torch
import torch.nn as nn
import torch.optim as optim
from torch.autograd import grad
import numpy as np
import matplotlib.pyplot as plt
from scipy.integrate import solve_ivp

# Generate training data for the damped pendulum
def damped_pendulum(t, y, b, c):
    q, p = y
    dqdt = p
    dpdt = -c * np.sin(q) - b * p
    return [dqdt, dpdt]

# True Parameters
true_b = 0.2  # True damping coefficient (unknown to the model)
c = 9.81  # Gravity
y0 = [np.pi / 2, 0]  # Initial condition
t_span = (0, 10)
t_eval = np.linspace(*t_span, 300)

# Solve the system
sol = solve_ivp(damped_pendulum, t_span, y0, t_eval=t_eval, args=(true_b, c))

# Add noise to data
noise_std = 0.05
q_noisy = sol.y[0] + noise_std * np.random.randn(*sol.y[0].shape)
p_noisy = sol.y[1] + noise_std * np.random.randn(*sol.y[1].shape)

# Convert data to PyTorch tensors
q_train = torch.tensor(q_noisy, dtype=torch.float32).reshape(-1, 1)
p_train = torch.tensor(p_noisy, dtype=torch.float32).reshape(-1, 1)
data_train = torch.cat((q_train, p_train), dim=1)

# Define the Hamiltonian Neural Network with learnable damping
class HamiltonianNN(nn.Module):
    def __init__(self):
        super(HamiltonianNN, self).__init__()
        self.net = nn.Sequential(
            nn.Linear(2, 32),
            nn.Tanh(),
            nn.Linear(32, 32),
            nn.Tanh(),
            nn.Linear(32, 1)  # Outputs the Hamiltonian
        )
        self.b = nn.Parameter(torch.tensor(0.5, dtype=torch.float32))  # Initial guess for damping

    def forward(self, q, p):
        H = self.net(torch.cat((q, p), dim=1))
        return H

# Initialize model, optimizer, and loss function
model = HamiltonianNN()
optimizer = optim.Adam(model.parameters(), lr=0.01)

lambda_data = 1e-2  # Weight for data loss

# Training loop
epochs = 50000
for epoch in range(epochs):
    optimizer.zero_grad()

    q, p = data_train[:, 0:1], data_train[:, 1:2]
    q.requires_grad_(True)
    p.requires_grad_(True)

    H = model(q, p)
    dH_dq = grad(H.sum(), q, create_graph=True)[0]
    dH_dp = grad(H.sum(), p, create_graph=True)[0]

    # Hamiltonian equations with learnable damping
    dq_pred = dH_dp
    dp_pred = -dH_dq - model.b * p

    # Physics-informed loss (PDE residual)
    loss_pde = torch.mean((dq_pred - p) ** 2 + (dp_pred + c * torch.sin(q) + model.b * p) ** 2)

    # Data loss (forcing network to match noisy data)
    loss_data = torch.mean((dq_pred - p) ** 2 + (dp_pred - (-c * torch.sin(q) - model.b * p)) ** 2)

    # Total loss
    loss = loss_pde + lambda_data * loss_data

    # Backpropagation
    loss.backward()
    optimizer.step()

    if epoch % 500 == 0:
        print(f"Epoch {epoch}, Loss: {loss.item()}, Learned b: {model.b.item()}")

# Test the learned Hamiltonian
q_test = torch.linspace(-np.pi, np.pi, 100).reshape(-1, 1)
p_test = torch.linspace(-2, 2, 100).reshape(-1, 1)
q_mesh, p_mesh = torch.meshgrid(q_test.flatten(), p_test.flatten())

q_input = q_mesh.reshape(-1, 1)
p_input = p_mesh.reshape(-1, 1)
H_pred = model(q_input, p_input).detach().numpy().reshape(100, 100)

# Plot the learned Hamiltonian
plt.figure(figsize=(8, 6))
plt.contourf(q_mesh.numpy(), p_mesh.numpy(), H_pred, levels=30, cmap="viridis")
plt.colorbar(label="Hamiltonian")
plt.xlabel("Angle (q)")
plt.ylabel("Momentum (p)")
plt.title(f"Learned Hamiltonian for the Damped Pendulum (b = {model.b.item():.4f})")
plt.show()

In [ ]:
# Re-import necessary libraries after execution state reset
import numpy as np
import matplotlib.pyplot as plt
from scipy.integrate import solve_ivp

# Define the damped pendulum system
def damped_pendulum(t, y, b, c):
    q, p = y
    dqdt = p
    dpdt = -c * np.sin(q) - b * p
    return [dqdt, dpdt]

# Parameters
true_b = 0.2  # True damping coefficient
learned_b = 0.18  # Placeholder learned value
c = 9.81  # Gravity
y0 = [np.pi / 2, 0]  # Initial condition
t_span = (0, 10)
t_eval = np.linspace(*t_span, 300)

# Solve for the true trajectory
sol_true = solve_ivp(damped_pendulum, t_span, y0, t_eval=t_eval, args=(true_b, c))
q_true, p_true = sol_true.y

# Generate noisy data
noise_std = 0.05
q_noisy = q_true + noise_std * np.random.randn(*q_true.shape)
p_noisy = p_true + noise_std * np.random.randn(*p_true.shape)

# Solve for the learned trajectory
sol_learned = solve_ivp(damped_pendulum, t_span, y0, t_eval=t_eval, args=(learned_b, c))
q_learned, p_learned = sol_learned.y

# Plot the phase space trajectories
plt.figure(figsize=(8, 6))

# True trajectory
plt.plot(q_true, p_true, label="True Trajectory", color="blue", linewidth=2)

# Noisy trajectory
plt.scatter(q_noisy, p_noisy, label="Noisy Data", color="red", s=10, alpha=0.6)

# Learned trajectory
plt.plot(q_learned, p_learned, label="Learned Trajectory", color="green", linestyle="dashed")

plt.xlabel("Angle (q)")
plt.ylabel("Momentum (p)")
plt.title("Phase Space Trajectory: True, Noisy, and Learned")
plt.legend()
plt.grid()
plt.show()

In [ ]:
# Re-import necessary libraries after execution state reset
import numpy as np
import matplotlib.pyplot as plt
from scipy.integrate import solve_ivp

# Define the damped pendulum system
def damped_pendulum(t, y, b, c):
    q, p = y
    dqdt = p
    dpdt = -c * np.sin(q) - b * p
    return [dqdt, dpdt]

# Parameters
true_b = 0.2  # True damping coefficient
learned_b = 0.18  # Placeholder learned value
c = 9.81  # Gravity
y0 = [np.pi / 2, 0]  # Initial condition
t_span = (0, 30)
t_eval = np.linspace(*t_span, 300)

# Solve for the true trajectory
sol_true = solve_ivp(damped_pendulum, t_span, y0, t_eval=t_eval, args=(true_b, c))
q_true, p_true = sol_true.y

# Generate noisy data
noise_std = 0.05
q_noisy = q_true + noise_std * np.random.randn(*q_true.shape)
p_noisy = p_true + noise_std * np.random.randn(*p_true.shape)

# Solve for the learned trajectory
sol_learned = solve_ivp(damped_pendulum, t_span, y0, t_eval=t_eval, args=(learned_b, c))
q_learned, p_learned = sol_learned.y

# Plot q(t) over time
plt.figure(figsize=(8, 5))
plt.plot(t_eval, q_true, label="True q(t)", color="blue", linewidth=2)
plt.scatter(t_eval, q_noisy, label="Noisy q(t)", color="red", s=10, alpha=0.6)
plt.plot(t_eval, q_learned, label="Learned q(t)", color="green", linestyle="dashed")
plt.xlabel("Time (s)")
plt.ylabel("Angle (q)")
plt.title("Angle Evolution Over Time with True, Noisy, and Learned Data")
plt.legend()
plt.grid()
plt.show()

# Plot p(t) over time
plt.figure(figsize=(8, 5))
plt.plot(t_eval, p_true, label="True p(t)", color="blue", linewidth=2)
plt.scatter(t_eval, p_noisy, label="Noisy p(t)", color="red", s=10, alpha=0.6)
plt.plot(t_eval, p_learned, label="Learned p(t)", color="green", linestyle="dashed")
plt.xlabel("Time (s)")
plt.ylabel("Momentum (p)")
plt.title("Momentum Evolution Over Time with True, Noisy, and Learned Data")
plt.legend()
plt.grid()
plt.show()

In [ ]:
import torch
import torch.nn as nn
import torch.optim as optim
from torch.autograd import grad
import numpy as np
import matplotlib.pyplot as plt
from scipy.integrate import solve_ivp

# Generate training data for the damped pendulum
def damped_pendulum(t, y, b, c):
    q, p = y
    dqdt = p
    dpdt = -c * np.sin(q) - b * p
    return [dqdt, dpdt]

# True Parameters
true_b = 0.2  # True damping coefficient (unknown to the model)
c = 9.81  # Gravity
y0 = [np.pi / 2, 0]  # Initial condition
t_span = (0, 10)
t_eval = np.linspace(*t_span, 300)

# Solve the system
sol = solve_ivp(damped_pendulum, t_span, y0, t_eval=t_eval, args=(true_b, c))

# Add noise to data
noise_std = 0.05
q_noisy = sol.y[0] + noise_std * np.random.randn(*sol.y[0].shape)
p_noisy = sol.y[1] + noise_std * np.random.randn(*sol.y[1].shape)

# Convert data to PyTorch tensors
q_train = torch.tensor(q_noisy, dtype=torch.float32).reshape(-1, 1)
p_train = torch.tensor(p_noisy, dtype=torch.float32).reshape(-1, 1)
data_train = torch.cat((q_train, p_train), dim=1)

# Define the Hamiltonian Neural Network with learnable damping
class HamiltonianNN(nn.Module):
    def __init__(self):
        super(HamiltonianNN, self).__init__()
        self.net = nn.Sequential(
            nn.Linear(2, 32),
            nn.Tanh(),
            nn.Linear(32, 32),
            nn.Tanh(),
            nn.Linear(32, 1)  # Outputs the Hamiltonian
        )
        self.b = nn.Parameter(torch.tensor(0.5, dtype=torch.float32))  # Initial guess for damping

    def forward(self, q, p):
        H = self.net(torch.cat((q, p), dim=1))
        return H

# Initialize model, optimizer, and loss function
model = HamiltonianNN()
optimizer = optim.Adam(model.parameters(), lr=0.01)

lambda_data = 1e-2  # Weight for data loss

# Training loop
epochs = 50000
for epoch in range(epochs):
    optimizer.zero_grad()

    q, p = data_train[:, 0:1], data_train[:, 1:2]
    q.requires_grad_(True)
    p.requires_grad_(True)

    H = model(q, p)
    dH_dq = grad(H.sum(), q, create_graph=True)[0]
    dH_dp = grad(H.sum(), p, create_graph=True)[0]

    # Hamiltonian equations with learnable damping
    dq_pred = dH_dp
    dp_pred = -dH_dq - model.b * p

    # Physics-informed loss (PDE residual)
    loss_pde = torch.mean((dq_pred - p) ** 2 + (dp_pred + c * torch.sin(q) + model.b * p) ** 2)

    # Data loss (forcing network to match noisy data)
    loss_data = torch.mean((dq_pred - p) ** 2 + (dp_pred - (-c * torch.sin(q) - model.b * p)) ** 2)

    # Total loss
    loss = loss_pde + lambda_data * loss_data

    # Backpropagation
    loss.backward()
    optimizer.step()

    if epoch % 500 == 0:
        print(f"Epoch {epoch}, Loss: {loss.item()}, Learned b: {model.b.item()}")

# Save the trained model
torch.save(model.state_dict(), "hamiltonian_nn_model.pth")
print(f"Training completed. Learned damping coefficient: {model.b.item():.4f}")

In [ ]:
t_span = (0, 50)
t_eval = np.linspace(*t_span, 300)

# Solve the system
sol = solve_ivp(damped_pendulum, t_span, y0, t_eval=t_eval, args=(true_b, c))

# Add noise to data
noise_std = 0.05
q_noisy = sol.y[0] + noise_std * np.random.randn(*sol.y[0].shape)
p_noisy = sol.y[1] + noise_std * np.random.randn(*sol.y[1].shape)

# Convert data to PyTorch tensors
q_train = torch.tensor(q_noisy, dtype=torch.float32).reshape(-1, 1)
p_train = torch.tensor(p_noisy, dtype=torch.float32).reshape(-1, 1)
data_train = torch.cat((q_train, p_train), dim=1)
# Phase plot for model vs ground truth
plt.figure(figsize=(8, 6))
plt.plot(sol.y[0], sol.y[1], label="Ground Truth", color="black", linestyle="dashed")
plt.scatter(q_noisy, p_noisy, label="Noisy Observations", color="red", s=5, alpha=0.6)

q_model = q_train.detach().numpy()
p_model = p_train.detach().numpy()
plt.plot(q_model, p_model, label="Model Prediction", color="blue", linestyle="solid")

plt.xlabel("Angle (q)")
plt.ylabel("Momentum (p)")
plt.legend()
plt.title("Phase Plot: Model vs Ground Truth")
plt.show()


In [ ]:
import torch
import numpy as np
import matplotlib.pyplot as plt
from scipy.integrate import solve_ivp

class HamiltonianTrue:
    def __init__(self):
        self.k = 2.4
        self.gamma = 0.0

    def hamiltonian_fn(self, coords):
        """
        Hamiltonian function for a damped pendulum.
        """
        q, p = torch.chunk(coords, 2, dim=-1)  # Ensure proper splitting
        H = self.k * (1 - torch.cos(q)) + p**2  # Standard pendulum Hamiltonian
        D = self.gamma * p**2  # Quadratic damping
        return H - D  # Energy loss due to dissipation

    def time_derivative(self, t, state):
        """
        Compute dq/dt and dp/dt using the Hamiltonian function and autograd.
        """
        state = torch.tensor(state, dtype=torch.float32, requires_grad=True).view(1, -1)  # Ensure shape
        H = self.hamiltonian_fn(state)  # Compute the Hamiltonian
        dH = torch.autograd.grad(H.sum(), state, create_graph=True)[0]  # Compute gradients

        dq_dt = dH[0, 1]  # ∂H/∂p
        dp_dt = -dH[0, 0] - self.gamma * dH[0, 1]  # -∂H/∂q - damping term
        return [dq_dt.item(), dp_dt.item()]

    def integrate(self, t_span=[0, 10], y0=[np.pi / 2, 0], resolution=1000):
        sol = solve_ivp(lambda t, y: self.time_derivative(t, y), t_span, y0, t_eval=np.linspace(*t_span, resolution))
        return sol.t, sol.y[0], sol.y[1]

    def get_field(self, xmin=-np.pi/2, xmax=np.pi/2, ymin=-np.pi/2, ymax=np.pi/2, gridsize=20):
        """
        Computes the vector field (q, p, dq/dt, dp/dt) for the dynamical system.

        Args:
            xmin, xmax: Range for q (angle).
            ymin, ymax: Range for p (momentum).
            gridsize: Number of points in each dimension.

        Returns:
            ys.T: Grid points.
            dydt.T: Corresponding velocity vectors (dq/dt, dp/dt).
        """
        # Create a grid in phase space
        b, a = np.meshgrid(np.linspace(xmin, xmax, gridsize), np.linspace(ymin, ymax, gridsize))
        ys = np.stack([b.flatten(), a.flatten()], axis=1)  # Shape (N, 2)

        # Compute the vector field at each grid point
        dydt = np.array([self.time_derivative(None, y) for y in ys])  # Shape (N, 2)

        return ys, dydt


In [ ]:
# Initialize system
hamiltonian_true = HamiltonianTrue()

# Get the vector field
field, directions = hamiltonian_true.get_field(gridsize=20)

# Plot configuration
fig, ax = plt.subplots(figsize=(6, 6))
ax.quiver(field[:, 0], field[:, 1], directions[:, 0], directions[:, 1], color="gray", angles='xy')

plt.xlabel("$q$ (angle)")
plt.ylabel("$p$ (momentum)")
plt.title("Phase Space Vector Field of Damped Pendulum")
plt.grid()
plt.show()

In [ ]:
hamiltonian_true = HamiltonianTrue()

def plot_phase_portrait(k=hamiltonian_true.k, gamma=hamiltonian_true.gamma, q_range=(-np.pi, np.pi), p_range=(-3, 3), grid_size=20):
    """
    Plots the phase portrait of the damped pendulum with a sample trajectory.
    """
    q_vals = np.linspace(q_range[0], q_range[1], grid_size)
    p_vals = np.linspace(p_range[0], p_range[1], grid_size)
    Q, P = np.meshgrid(q_vals, p_vals)

    dQ, dP = np.zeros(Q.shape), np.zeros(P.shape)
    for i in range(Q.shape[0]):
        for j in range(Q.shape[1]):
            dQ[i, j], dP[i, j] = hamiltonian_true.time_derivative(0, [Q[i, j], P[i, j]])

    plt.figure(figsize=(8, 6))
    plt.streamplot(Q, P, dQ, dP, color=np.sqrt(dQ**2 + dP**2), cmap='plasma', density=1.2)

    # Solve and plot a single trajectory
    t_span = [0, 10]
    y0 = [np.pi / 2, 0]  # Initial condition: (q0, p0)
    sol = hamiltonian_true.integrate(t_span, y0)
    plt.plot(sol[1], sol[2], 'b', label="Sample Path")

    plt.xlabel("Angle q (rad)")
    plt.ylabel("Momentum p")
    plt.title(f"Phase Portrait of Damped Pendulum (k={k}, gamma={gamma})")
    plt.legend()
    plt.grid()
    plt.show()

    # Plot Time Response
    plt.figure(figsize=(10, 4))
    plt.plot(sol[0], sol[1], label="Angle q (rad)")
    plt.plot(sol[0], sol[2], label="Angular Velocity p (rad/s)")
    plt.xlabel("Time (s)")
    plt.ylabel("State Variables")
    plt.title(f"Damped Pendulum Time Response (k={k}, gamma={gamma})")
    plt.legend()
    plt.grid()
    plt.show()



# Run the phase plot function
plot_phase_portrait()

In [ ]:
# Use the existing HamiltonianTrue class
hamiltonian_true = HamiltonianTrue()

def generate_noisy_data(samples=100, noise_std=0.05, t_span = [0, 10], y0 = [np.pi / 2, 0]):
    """
    Generates synthetic data from HamiltonianTrue and adds Gaussian noise.

    Args:
        samples: Number of samples to generate.
        noise_std: Standard deviation of the noise.

    Returns:
        Torch tensors for training: (q, p, dq/dt, dp/dt)
    """
    t_eval = np.linspace(*t_span, samples)

    # Integrate the true system
    sol = hamiltonian_true.integrate(t_span, y0, resolution=samples)
    q, p = sol[1], sol[2]

    dq_dt, dp_dt = np.array([hamiltonian_true.time_derivative(0, [q_i, p_i]) for q_i, p_i in zip(q, p)]).T

    # # Compute derivatives
    # dq_dt, dp_dt = np.gradient(q, t_eval), np.gradient(p, t_eval)

    # Add Gaussian noise
    q += np.random.normal(0, noise_std, q.shape)
    p += np.random.normal(0, noise_std, p.shape)
    dq_dt += np.random.normal(0, noise_std, dq_dt.shape)
    dp_dt += np.random.normal(0, noise_std, dp_dt.shape)

    # Convert to Torch tensors
    q, p, dq_dt, dp_dt = map(lambda x: torch.tensor(x, dtype=torch.float32), [q, p, dq_dt, dp_dt])

    return q, p, dq_dt, dp_dt, t_eval

# Generate dataset
q_noisy, p_noisy, dq_dt_noisy, dp_dt_noisy, t_noisy = generate_noisy_data(samples=10, noise_std=0.05, t_span = [0, 5], y0 = [np.pi / 2, 0])
# q, p, dq_dt, dp_dt, t_eval = generate_noisy_data(noise_std=0.0, samples=1000)

field = hamiltonian_true.get_field(gridsize=15)

# plot config
fig = plt.figure(figsize=(6, 6), facecolor='white')

plt.scatter(p_noisy,q_noisy,c=t_noisy,s=14, label='data')
plt.plot(q,p, label='ground truth')
plt.quiver(field[0][:,0], field[0][:,1], field[1][:,0], field[1][:,1],
           cmap='gray_r', color=(.5,.5,.5))
plt.xlabel("$q$", fontsize=14)
plt.ylabel("$p$", rotation=0, fontsize=14)
plt.title(f"Dynamics Damped Pendulum (k={hamiltonian_true.k}, gamma={hamiltonian_true.gamma})\n number of data points:{len(t_noisy)}", fontsize=14)
plt.legend(loc='upper right')
plt.axis('equal')

plt.tight_layout() ; plt.show()

In [ ]:
from torch.utils.data import DataLoader, TensorDataset

# Prepare dataset
dataset = TensorDataset(torch.stack([q_noisy, p_noisy], dim=1), torch.stack([dq_dt_noisy, dp_dt_noisy], dim=1))
train_loader = DataLoader(dataset, batch_size=min(32, len(q_noisy)//4), shuffle=True)

In [ ]:
import torch.nn as nn
# Define Multi-Layer Perceptron (MLP)
# Corrected MLP class
class MLP(nn.Module):
    def __init__(self, input_dim, output_dim, hidden_dim):
        """
        Multi-Layer Perceptron for the HNN.

        Args:
            input_dim: Number of input features.
            output_dim: Number of output features.
            hidden_dim: Number of hidden neurons.
        """
        super().__init__()
        self.net = nn.Sequential(
            nn.Linear(input_dim, hidden_dim),
            nn.Tanh(),
            nn.Linear(hidden_dim, hidden_dim),
            nn.Tanh(),
            nn.Linear(hidden_dim, output_dim)
        )

    def forward(self, x, t=None):
        inputs = torch.cat([x, t], axis=-1) if t is not None else x
        return self.net(inputs)


    def integrate(self, t_span=[0, 10], y0=[np.pi / 2, 0], resolution=1000):
        """
        Integrates the learned system dynamics over time using solve_ivp.

        Args:
            t_span: Time range for integration.
            y0: Initial conditions [q0, p0].
            resolution: Number of time steps.

        Returns:
            t, q, p: Time steps and corresponding trajectories.
        """
        sol = solve_ivp(
            lambda t, y: self.forward(torch.tensor(y, dtype=torch.float32, requires_grad=True).view(1, -1)).detach().numpy().flatten(),
            t_span, y0, t_eval=np.linspace(*t_span, resolution)
        )
        return sol.t, sol.y[0], sol.y[1]

# Define Hamiltonian Neural Network (HNN)
class HNN(nn.Module):
    def __init__(self, input_dim, hidden_dim):
        super().__init__()
        self.mlp = MLP(input_dim, 1, hidden_dim)

    def forward(self, x, t=None):
        inputs = torch.cat([x, t], axis=-1) if t is not None else x
        H = self.mlp(inputs)[..., 0]
        H_grads = torch.autograd.grad(H.sum(), x, create_graph=True)[0]
        dHdq, dHdp = torch.split(H_grads, H_grads.shape[-1] // 2, dim=1)
        return torch.cat([dHdp, -dHdq], axis=-1)

    def predict_hamiltonian(self, x, t=None):
        return self.mlp(x, t)

    def integrate(self, t_span=[0, 10], y0=[np.pi / 2, 0], resolution=1000):
        """
        Integrates the learned system dynamics over time using solve_ivp.

        Args:
            t_span: Time range for integration.
            y0: Initial conditions [q0, p0].
            resolution: Number of time steps.

        Returns:
            t, q, p: Time steps and corresponding trajectories.
        """
        sol = solve_ivp(
            lambda t, y: self.forward(torch.tensor(y, dtype=torch.float32, requires_grad=True).view(1, -1)).detach().numpy().flatten(),
            t_span, y0, t_eval=np.linspace(*t_span, resolution)
        )
        return sol.t, sol.y[0], sol.y[1]

    def save_model(self, model_path="hnn_weights.pth"):
        """Save the model's state_dict to a file."""
        torch.save(self.state_dict(), model_path)
        print(f"Model weights saved to {model_path}")

    def load_model(self, model_path="hnn_weights.pth"):
        """Load the model's state_dict from a file."""
        self.load_state_dict(torch.load(model_path))
        self.eval()  # Set the model to evaluation mode
        print(f"Model weights loaded from {model_path}")


class DHNN(nn.Module):
    def __init__(self, input_dim, hidden_dim):
        super().__init__()
        self.mlp_h = MLP(input_dim, 1, hidden_dim)  # Conservative component
        self.mlp_d = MLP(input_dim, 1, hidden_dim)  # Dissipative component

    def forward(self, x, t=None, as_separate=False):
        inputs = torch.cat([x, t], axis=-1) if t is not None else x
        D = self.mlp_d(inputs)
        H = self.mlp_h(inputs)

        # Compute gradients
        irr_component = torch.autograd.grad(D.sum(), x, create_graph=True, retain_graph=True)[0]
        rot_component = torch.autograd.grad(H.sum(), x, create_graph=True, retain_graph=True)[0]

        # Compute time derivatives
        dHdq, dHdp = torch.split(rot_component, rot_component.shape[-1] // 2, dim=1)
        q_dot_hat, p_dot_hat = dHdp, -dHdq
        rot_component = torch.cat([q_dot_hat, p_dot_hat], axis=-1)

        if as_separate:
            return irr_component, rot_component

        return irr_component + rot_component

    def predict_hamiltonian(self, x, t=None):
        x = x.view(-1, 2)  # Ensure correct shape
        predicted_H = self.mlp_h(x)
        predicted_D = self.mlp_d(x)
        total_H = predicted_H - predicted_D
        return total_H

    def integrate(self, t_span=[0, 10], y0=[np.pi / 2, 0], resolution=1000):
        """
        Integrates the learned system dynamics over time using solve_ivp.

        Args:
            t_span: Time range for integration.
            y0: Initial conditions [q0, p0].
            resolution: Number of time steps.

        Returns:
            t, q, p: Time steps and corresponding trajectories.
        """
        sol = solve_ivp(
            lambda t, y: self.forward(torch.tensor(y, dtype=torch.float32, requires_grad=True).view(1, -1)).detach().numpy().flatten(),
            t_span, y0, t_eval=np.linspace(*t_span, resolution)
        )
        return sol.t, sol.y[0], sol.y[1]

    def save_model(self, model_path="dhnn_weights.pth"):
        torch.save(self.state_dict(), model_path)
        print(f"Model weights saved to {model_path}")

    def load_model(self, model_path="dhnn_weights.pth"):
        self.load_state_dict(torch.load(model_path))
        self.eval()
        print(f"Model weights loaded from {model_path}")

In [ ]:
from tqdm import tqdm


# Define Loss Function and Optimizer
def train_hnn(model, train_loader, epochs=100):
    optimizer = torch.optim.Adam(model.parameters(), lr=0.01, weight_decay=1e-5)
    scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(optimizer, 'min', patience=1000, factor=0.5)
    loss_fn = nn.MSELoss()
    loss_history = []
    increments_per_epoch = 100

    with tqdm(total=epochs) as pbar:
        total_loss = 0
        for epoch in range(epochs):
            for batch in train_loader:
                (x_batch, y_batch) = batch  # (q, p), (dq/dt, dp/dt)

                x_batch.requires_grad = True  # Needed for autograd
                y_pred = model(x_batch)  # Predict dynamics

                loss = loss_fn(y_pred, y_batch)  # Compute loss
                optimizer.zero_grad()
                loss.backward()
                optimizer.step()
                scheduler.step(loss)
                total_loss += loss.item()

            if epoch % increments_per_epoch == 0:
                loss_history.append(loss.item())
                # Update pbar description with current loss and the last learning rate
                pbar.set_description(f'Epoch {epoch}, Loss: {loss.item():.4f}, LR: {optimizer.param_groups[0]["lr"]:.6f}')
            pbar.update()

        # Plotting the loss history
    plt.figure(figsize=(10, 5))
    plt.semilogy(np.arange(0, epochs, increments_per_epoch), loss_history, label='Training Loss')
    plt.xlabel('Epochs')
    plt.ylabel('Loss')
    plt.title('Training Loss of HNN over Epochs')
    plt.legend()
    plt.grid(True)
    plt.show()

    print("Training complete!")

In [ ]:
# Initialize and train the HNN
input_dim = 2
hidden_dim = 64
hnn_model = HNN(input_dim, hidden_dim)
train_hnn(hnn_model, train_loader, epochs=5000)

In [ ]:
hamiltonian_true = HamiltonianTrue()

def evaluate_hnn(model, model_name='HNN', k=hamiltonian_true.k, gamma=hamiltonian_true.gamma):
    """
    Evaluates the HNN model and plots predictions vs true dynamics.
    """
    # Integrate model and true system
    t_span=[0, 50]
    y0=[np.pi / 2, 0]
    resolution=1000
    t_pred, q_pred, p_pred = model.integrate(t_span=t_span, y0=y0, resolution=resolution)
    t_true, q_true, p_true = hamiltonian_true.integrate(t_span=t_span, y0=y0, resolution=resolution)

    # Create a subplot grid (2 rows, 2 columns) for better organization
    fig, axes = plt.subplots(2, 2, figsize=(14, 10))

    # Plot q(t) - True vs Predicted
    axes[0, 0].plot(t_true, q_true, label="True q", linestyle='-', color='blue', linewidth=2)
    axes[0, 0].plot(t_pred, q_pred, label="Predicted q", linestyle='--', color='red', linewidth=2)
    axes[0, 0].scatter(t_noisy, q_noisy, label="Data", c=t_noisy, s=10, cmap="viridis", alpha=0.7)
    axes[0, 0].set_xlabel("Time Steps")
    axes[0, 0].set_ylabel("q")
    axes[0, 0].legend()
    axes[0, 0].set_title(f"{model_name} Predictions vs True: q(t)")
    axes[0, 0].grid(True)

    # Plot p(t) - True vs Predicted
    axes[0, 1].plot(t_true, p_true, label="True p", linestyle='-', color='blue', linewidth=2)
    axes[0, 1].plot(t_pred, p_pred, label="Predicted p", linestyle='--', color='red', linewidth=2)
    axes[0, 1].scatter(t_noisy, p_noisy, label="Data", c=t_noisy, s=10, cmap="plasma", alpha=0.7)
    axes[0, 1].set_xlabel("Time Steps")
    axes[0, 1].set_ylabel("p")
    axes[0, 1].legend()
    axes[0, 1].set_title(f"{model_name} Predictions vs True: p(t)")
    axes[0, 1].grid(True)

    # Plot phase space (q, p) - True vs Predicted
    axes[1, 0].plot(q_true, p_true, label="True", linestyle='-', color='blue', linewidth=2)
    axes[1, 0].plot(q_pred, p_pred, label="Predicted", linestyle='--', color='red', linewidth=2)
    scatter = axes[1, 0].scatter(q_noisy, p_noisy, c=t_noisy, s=10, cmap="coolwarm", alpha=0.7, label='Data')
    axes[1, 0].set_xlabel("q")
    axes[1, 0].set_ylabel("p")
    axes[1, 0].legend()
    axes[1, 0].set_title(f"{model_name} Phase Space: Predictions vs True")
    axes[1, 0].grid(True)
    fig.colorbar(scatter, ax=axes[1, 0], label="Time")
    try:
        # Compute and plot Hamiltonian evolution
        coords_true = torch.stack([torch.tensor(q_true, dtype=torch.float32),
                                   torch.tensor(p_true, dtype=torch.float32)], dim=1)
        true_H = hamiltonian_true.hamiltonian_fn(coords_true).detach().numpy()

        coords_pred = torch.stack([torch.tensor(q_pred, dtype=torch.float32),
                                   torch.tensor(p_pred, dtype=torch.float32)], dim=1)
        predicted_H = model.predict_hamiltonian(coords_pred).detach().numpy()

        axes[1, 1].plot(true_H, label="True Hamiltonian", color='purple', linewidth=2)
        axes[1, 1].plot(predicted_H, label="Predicted Hamiltonian", linestyle="dashed", color='orange', linewidth=2)
        axes[1, 1].set_xlabel("Time Steps")
        axes[1, 1].set_ylabel("Hamiltonian Value")
        axes[1, 1].set_title("Hamiltonian Evolution Over Time")
        axes[1, 1].legend()
        axes[1, 1].grid(True)
    except:
        print("Hamiltonian prediction failed")

    plt.suptitle(f"{model_name} Results (k={k} and gamma={gamma})")
    plt.tight_layout()

    plt.show()

# Re-run evaluation
evaluate_hnn(hnn_model)

In [ ]:
# Initialize and train the HNN
input_dim = 2
hidden_dim = 64
dhnn_model = DHNN(input_dim, hidden_dim)
train_hnn(dhnn_model, train_loader, epochs=5000)
# Re-run evaluation
evaluate_hnn(dhnn_model, model_name='DHNN')

In [ ]:
# Initialize and train the HNN
input_dim = 2
hidden_dim = 64
nn_model = MLP(input_dim, 2, hidden_dim)
train_hnn(nn_model, train_loader, epochs=5000)
# Re-run evaluation
evaluate_hnn(nn_model, model_name='MLP')